### Decision tree Estimator on merged_emp data 

- This Python notebook demonstrates creating an ML Pipeline to preprocess a dataset, train a Machine Learning model, and make predictions.

- Data: The dataset contains    merged_emp data  

- Goal: We want to learn to predict  deaths  from features such as patient data (comprising of Adult_smoking_percentage,	Adult_obesity_percentage and Excessive_drinking_percentage), various healthcare data like hospitals, physician, nurses, surgean specialities, etc., socio econonmic factors like life rank, quality of life, social-ecomonica factors rank, physical environment rank, etc. and other features like popluation, etc.  

- Approach: We will use Spark ML Pipelines, which help users piece together parts of a workflow such as feature processing and model training. We will also demonstrate model selection (a.k.a. hyperparameter tuning) using Cross Validation in order to fine-tune and improve our ML model.

In [2]:
%sh 
pip install mleap

Requirement already satisfied: mleap in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (0.8.1)
Requirement already satisfied: argparse>=1.1 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from mleap) (1.4.0)
Requirement already satisfied: nose-exclude>=0.5.0 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from mleap) (0.5.0)
Requirement already satisfied: scipy>=0.13.0b1 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from mleap) (1.2.1)
Requirement already satisfied: numpy>=1.8.2 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from mleap) (1.18.5)
Requirement already satisfied: six>=1.10.0 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from mleap) (1.12.0)
Requirement already satisfied: pandas>=0.18.1 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from mleap) (1.0.4)
Requirement already satisfied: scikit-learn>=0.18.dev0 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from mleap) (0.20.3)
Requirement already satisfied: nose in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from nose-exclude>=0.5.0->mleap) (1.3.7)
Requirement already satisfied: python-dateutil>=2.6.1 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from pandas>=0.18.1->mleap) (2.8.0)
Requirement already satisfied: pytz>=2017.2 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from pandas>=0.18.1->mleap) (2018.9)

In [3]:
from pyspark.sql.functions import log

In [4]:
# read data from the output of exploratory data analysis which is in parquet file format
df = spark.read.parquet('/databricks/driver/spark_merged_emp_modeling1.parquet')

In [5]:
display(df)

county cases deaths POP_ESTIMATE_2018 All_Specialties_AAMC Total_nurse_practitioners_2019 Total_physician_assistants_2019 Total_Hospitals_2019 Total_Primary_Care_Physicians_2019 Surgery_specialists_2019 Emergency_Medicine_specialists_2019 Total_Specialist_Physicians_2019 ICU_Beds pop_fraction Length_of_Life_rank Quality_of_Life_rank Health_Behaviors_rank Clinical_Care_rank Social_Economic_Factors_rank Physical_Environment_rank Adult_smoking_percentage Adult_obesity_percentage Excessive_drinking_percentage Population_per_sq_mile House_per_sq_mile Unemployed_2019 Unemployment_rate_2019 Median_Household_Income_2018 Med_HH_Income_Percent_of_State_Total_2018 Lee 7.117022517792556 0.5833625014584063 17142.0 2.2945925621281065 0.4171807667133357 0.20632844143040488 0.013571651557577879 1.257836399486641 0.1581392439621981 0.14319075819624313 1.2690477639715319 0.0 0.001685835 41.0 46.0 44.0 41.0 42.0 41.0 21.0 40.0 13.0 46.9 19.0 266.0 4.0 33199.0 63.29767965 Lexington 1.667615716261287 0.08473657094823613 295032.0 2.2945925621627485 0.4171807668320725 0.20632844145719786 0.013571651532715095 1.2578363994414166 0.158139243980314 0.14319075822283683 1.2690477636324196 0.18642045608611948 0.029015011 9.0 10.0 11.0 6.0 3.0 7.0 16.0 32.0 19.0 375.4 163.0 3510.0 2.3 60627.0 115.5922897 Marion 1.5464415735043011 0.12887013112535842 31039.0 2.294592562260382 0.41718076677728017 0.20632844144463416 0.013571651535165435 1.2578363993685362 0.15813924395115822 0.14319075820741647 1.2690477637810496 0.32217532781339603 0.00305254 40.0 45.0 41.0 44.0 43.0 19.0 20.0 44.0 14.0 67.6 30.6 564.0 4.3 34365.0 65.52079163 Marlboro 2.272899462080461 0.0 26398.0 2.294592562315327 0.41718076672475185 0.20632844143495718 0.013571651526630805 1.2578363993484354 0.15813924395787562 0.1431907582013789 1.2690477638457458 0.0 0.002596119 43.0 39.0 40.0 39.0 45.0 44.0 21.0 39.0 15.0 60.3 25.2 444.0 4.8 33534.0 63.93639536 McCormick 0.7438894792773645 0.10626992561105207 9410.0 2.2945925621679066 0.41718076673751325 0.206328441445271 0.013571651540913922 1.2578363995749204 0.15813924399574922 0.14319075823591926 1.2690477640807651 0.0 9.25429E-4 46.0 25.0 9.0 4.0 34.0 13.0 17.0 34.0 14.0 28.5 15.2 104.0 3.1 44683.0 85.19323533 Newberry 0.8047767393561787 0.02596053997923157 38520.0 2.294592562305296 0.41718076661474557 0.2063284414330218 0.013571651531671856 1.2578363995327102 0.1581392439771547 0.14319075822949118 1.269047763759086 0.181723779854621 0.003788261 10.0 21.0 23.0 21.0 15.0 16.0 18.0 36.0 16.0 59.5 28.4 514.0 2.7 48029.0 91.57276592 Oconee 0.49761400464439737 0.0 78374.0 2.2945925625845303 0.41718076670834714 0.2063284414474188 0.01357165152984408 1.257836399443693 0.15813924400949295 0.14319075815959373 1.2690477637992192 0.15311200142904535 0.007707715 16.0 4.0 14.0 12.0 12.0 15.0 17.0 32.0 16.0 118.6 61.9 971.0 2.8 50529.0 96.33930104 Orangeburg 1.2193158027929234 0.023005958543262706 86934.0 2.294592562173603 0.41718076667356846 0.20632844146133847 0.013571651528745943 1.2578363988773091 0.15813924390917247 0.14319075816136378 1.2690477638208295 0.23005958543262706 0.00854955 34.0 38.0 27.0 26.0 38.0 37.0 17.0 41.0 13.0 83.6 38.4 1655.0 4.8 37134.0 70.80020591 Pickens 0.6803428928179802 0.008004034033152708 124937.0 2.294592562651576 0.41718076670642007 0.20632844145449308 0.013571651536374333 1.257836399145169 0.1581392439389452 0.14319075822214394 1.2690477640730926 0.12006051049729063 0.012286967 12.0 8.0 6.0 7.0 9.0 33.0 17.0 32.0 18.0 240.2 103.2 1604.0 2.8 48794.0 93.03132567 Richland 2.814924163482691 0.142314075103238 414576.0 2.294592562280499 0.4171807666145652 0.20632844144378837 0.013571651533132646 1.2578363993574158 0.15813924397456677 0.1431907582204469 1.2690477637393385 0.5089537262166648 0.040771601 11.0 14.0 17.0 3.0 21.0 27.0 16.0 33.0 19.0 507.9 213.6 5579.0 2.8 52611.0 100.3088715 Saluda 4.478193146417445 0.0 20544.0 2.2945925623052963 0.4171807667445483 0.20632844144275703 0.013571651528426789 1.2578363994353583 0.15813924396

In [6]:
df_temp = df
from pyspark.sql.functions import col

#renaming column deaths in order to rearrange it to the end of the table.
df = df.withColumnRenamed('deaths', 'zlabel')

In [7]:
#sort columns according to column name
df = df.select(sorted(df.columns))

In [8]:
df.count()

Out[322]: 2920

In [9]:
df.dtypes

Out[323]: [('Adult_obesity_percentage', 'double'),
 ('Adult_smoking_percentage', 'double'),
 ('All_Specialties_AAMC', 'double'),
 ('Clinical_Care_rank', 'double'),
 ('Emergency_Medicine_specialists_2019', 'double'),
 ('Excessive_drinking_percentage', 'double'),
 ('Health_Behaviors_rank', 'double'),
 ('House_per_sq_mile', 'double'),
 ('ICU_Beds', 'double'),
 ('Length_of_Life_rank', 'double'),
 ('Med_HH_Income_Percent_of_State_Total_2018', 'double'),
 ('Median_Household_Income_2018', 'double'),
 ('POP_ESTIMATE_2018', 'double'),
 ('Physical_Environment_rank', 'double'),
 ('Population_per_sq_mile', 'double'),
 ('Quality_of_Life_rank', 'double'),
 ('Social_Economic_Factors_rank', 'double'),
 ('Surgery_specialists_2019', 'double'),
 ('Total_Hospitals_2019', 'double'),
 ('Total_Primary_Care_Physicians_2019', 'double'),
 ('Total_Specialist_Physicians_2019', 'double'),
 ('Total_nurse_practitioners_2019', 'double'),
 ('Total_physician_assistants_2019', 'double'),
 ('Unemployed_2019', 'double'),
 ('Unemployment_rate_2019', 'double'),
 ('cases', 'double'),
 ('county', 'string'),
 ('pop_fraction', 'double'),
 ('zlabel', 'double')]

In [10]:
display(df)

Adult_obesity_percentage Adult_smoking_percentage All_Specialties_AAMC Clinical_Care_rank Emergency_Medicine_specialists_2019 Excessive_drinking_percentage Health_Behaviors_rank House_per_sq_mile ICU_Beds Length_of_Life_rank Med_HH_Income_Percent_of_State_Total_2018 Median_Household_Income_2018 POP_ESTIMATE_2018 Physical_Environment_rank Population_per_sq_mile Quality_of_Life_rank Social_Economic_Factors_rank Surgery_specialists_2019 Total_Hospitals_2019 Total_Primary_Care_Physicians_2019 Total_Specialist_Physicians_2019 Total_nurse_practitioners_2019 Total_physician_assistants_2019 Unemployed_2019 Unemployment_rate_2019 cases county pop_fraction zlabel 40.0 21.0 2.2945925621281065 41.0 0.14319075819624313 13.0 44.0 19.0 0.0 41.0 63.29767965 33199.0 17142.0 41.0 46.9 46.0 42.0 0.1581392439621981 0.013571651557577879 1.257836399486641 1.2690477639715319 0.4171807667133357 0.20632844143040488 266.0 4.0 7.117022517792556 Lee 0.001685835 0.5833625014584063 32.0 16.0 2.2945925621627485 6.0 0.14319075822283683 19.0 11.0 163.0 0.18642045608611948 9.0 115.5922897 60627.0 295032.0 7.0 375.4 10.0 3.0 0.158139243980314 0.013571651532715095 1.2578363994414166 1.2690477636324196 0.4171807668320725 0.20632844145719786 3510.0 2.3 1.667615716261287 Lexington 0.029015011 0.08473657094823613 44.0 20.0 2.294592562260382 44.0 0.14319075820741647 14.0 41.0 30.6 0.32217532781339603 40.0 65.52079163 34365.0 31039.0 19.0 67.6 45.0 43.0 0.15813924395115822 0.013571651535165435 1.2578363993685362 1.2690477637810496 0.41718076677728017 0.20632844144463416 564.0 4.3 1.5464415735043011 Marion 0.00305254 0.12887013112535842 39.0 21.0 2.294592562315327 39.0 0.1431907582013789 15.0 40.0 25.2 0.0 43.0 63.93639536 33534.0 26398.0 44.0 60.3 39.0 45.0 0.15813924395787562 0.013571651526630805 1.2578363993484354 1.2690477638457458 0.41718076672475185 0.20632844143495718 444.0 4.8 2.272899462080461 Marlboro 0.002596119 0.0 34.0 17.0 2.2945925621679066 4.0 0.14319075823591926 14.0 9.0 15.2 0.0 46.0 85.19323533 44683.0 9410.0 13.0 28.5 25.0 34.0 0.15813924399574922 0.013571651540913922 1.2578363995749204 1.2690477640807651 0.41718076673751325 0.206328441445271 104.0 3.1 0.7438894792773645 McCormick 9.25429E-4 0.10626992561105207 36.0 18.0 2.294592562305296 21.0 0.14319075822949118 16.0 23.0 28.4 0.181723779854621 10.0 91.57276592 48029.0 38520.0 16.0 59.5 21.0 15.0 0.1581392439771547 0.013571651531671856 1.2578363995327102 1.269047763759086 0.41718076661474557 0.2063284414330218 514.0 2.7 0.8047767393561787 Newberry 0.003788261 0.02596053997923157 32.0 17.0 2.2945925625845303 12.0 0.14319075815959373 16.0 14.0 61.9 0.15311200142904535 16.0 96.33930104 50529.0 78374.0 15.0 118.6 4.0 12.0 0.15813924400949295 0.01357165152984408 1.257836399443693 1.2690477637992192 0.41718076670834714 0.2063284414474188 971.0 2.8 0.49761400464439737 Oconee 0.007707715 0.0 41.0 17.0 2.294592562173603 26.0 0.14319075816136378 13.0 27.0 38.4 0.23005958543262706 34.0 70.80020591 37134.0 86934.0 37.0 83.6 38.0 38.0 0.15813924390917247 0.013571651528745943 1.2578363988773091 1.2690477638208295 0.41718076667356846 0.20632844146133847 1655.0 4.8 1.2193158027929234 Orangeburg 0.00854955 0.023005958543262706 32.0 17.0 2.294592562651576 7.0 0.14319075822214394 18.0 6.0 103.2 0.12006051049729063 12.0 93.03132567 48794.0 124937.0 33.0 240.2 8.0 9.0 0.1581392439389452 0.013571651536374333 1.257836399145169 1.2690477640730926 0.41718076670642007 0.20632844145449308 1604.0 2.8 0.6803428928179802 Pickens 0.012286967 0.008004034033152708 33.0 16.0 2.294592562280499 3.0 0.1431907582204469 19.0 17.0 213.6 0.5089537262166648 11.0 100.3088715 52611.0 414576.0 27.0 507.9 14.0 21.0 0.15813924397456677 0.013571651533132646 1.2578363993574158 1.2690477637393385 0.4171807666145652 0.20632844144378837 5579.0 2.8 2.814924163482691 Richland 0.040771601 0.142314075103238 38.0 19.0 2.2945925623052963 45.0 0.1431907582262461 14.0 22.0 20.5 0.0 2.0 87.7404717 46019.0 20544.0 32.0 43.9 24.0 19.0 0.15813924396417445 0.013

In [11]:
#rename column back to label
df = df.withColumnRenamed('zlabel', 'label')

In [12]:
display(df)

Adult_obesity_percentage Adult_smoking_percentage All_Specialties_AAMC Clinical_Care_rank Emergency_Medicine_specialists_2019 Excessive_drinking_percentage Health_Behaviors_rank House_per_sq_mile ICU_Beds Length_of_Life_rank Med_HH_Income_Percent_of_State_Total_2018 Median_Household_Income_2018 POP_ESTIMATE_2018 Physical_Environment_rank Population_per_sq_mile Quality_of_Life_rank Social_Economic_Factors_rank Surgery_specialists_2019 Total_Hospitals_2019 Total_Primary_Care_Physicians_2019 Total_Specialist_Physicians_2019 Total_nurse_practitioners_2019 Total_physician_assistants_2019 Unemployed_2019 Unemployment_rate_2019 cases county pop_fraction label 40.0 21.0 2.2945925621281065 41.0 0.14319075819624313 13.0 44.0 19.0 0.0 41.0 63.29767965 33199.0 17142.0 41.0 46.9 46.0 42.0 0.1581392439621981 0.013571651557577879 1.257836399486641 1.2690477639715319 0.4171807667133357 0.20632844143040488 266.0 4.0 7.117022517792556 Lee 0.001685835 0.5833625014584063 32.0 16.0 2.2945925621627485 6.0 0.14319075822283683 19.0 11.0 163.0 0.18642045608611948 9.0 115.5922897 60627.0 295032.0 7.0 375.4 10.0 3.0 0.158139243980314 0.013571651532715095 1.2578363994414166 1.2690477636324196 0.4171807668320725 0.20632844145719786 3510.0 2.3 1.667615716261287 Lexington 0.029015011 0.08473657094823613 44.0 20.0 2.294592562260382 44.0 0.14319075820741647 14.0 41.0 30.6 0.32217532781339603 40.0 65.52079163 34365.0 31039.0 19.0 67.6 45.0 43.0 0.15813924395115822 0.013571651535165435 1.2578363993685362 1.2690477637810496 0.41718076677728017 0.20632844144463416 564.0 4.3 1.5464415735043011 Marion 0.00305254 0.12887013112535842 39.0 21.0 2.294592562315327 39.0 0.1431907582013789 15.0 40.0 25.2 0.0 43.0 63.93639536 33534.0 26398.0 44.0 60.3 39.0 45.0 0.15813924395787562 0.013571651526630805 1.2578363993484354 1.2690477638457458 0.41718076672475185 0.20632844143495718 444.0 4.8 2.272899462080461 Marlboro 0.002596119 0.0 34.0 17.0 2.2945925621679066 4.0 0.14319075823591926 14.0 9.0 15.2 0.0 46.0 85.19323533 44683.0 9410.0 13.0 28.5 25.0 34.0 0.15813924399574922 0.013571651540913922 1.2578363995749204 1.2690477640807651 0.41718076673751325 0.206328441445271 104.0 3.1 0.7438894792773645 McCormick 9.25429E-4 0.10626992561105207 36.0 18.0 2.294592562305296 21.0 0.14319075822949118 16.0 23.0 28.4 0.181723779854621 10.0 91.57276592 48029.0 38520.0 16.0 59.5 21.0 15.0 0.1581392439771547 0.013571651531671856 1.2578363995327102 1.269047763759086 0.41718076661474557 0.2063284414330218 514.0 2.7 0.8047767393561787 Newberry 0.003788261 0.02596053997923157 32.0 17.0 2.2945925625845303 12.0 0.14319075815959373 16.0 14.0 61.9 0.15311200142904535 16.0 96.33930104 50529.0 78374.0 15.0 118.6 4.0 12.0 0.15813924400949295 0.01357165152984408 1.257836399443693 1.2690477637992192 0.41718076670834714 0.2063284414474188 971.0 2.8 0.49761400464439737 Oconee 0.007707715 0.0 41.0 17.0 2.294592562173603 26.0 0.14319075816136378 13.0 27.0 38.4 0.23005958543262706 34.0 70.80020591 37134.0 86934.0 37.0 83.6 38.0 38.0 0.15813924390917247 0.013571651528745943 1.2578363988773091 1.2690477638208295 0.41718076667356846 0.20632844146133847 1655.0 4.8 1.2193158027929234 Orangeburg 0.00854955 0.023005958543262706 32.0 17.0 2.294592562651576 7.0 0.14319075822214394 18.0 6.0 103.2 0.12006051049729063 12.0 93.03132567 48794.0 124937.0 33.0 240.2 8.0 9.0 0.1581392439389452 0.013571651536374333 1.257836399145169 1.2690477640730926 0.41718076670642007 0.20632844145449308 1604.0 2.8 0.6803428928179802 Pickens 0.012286967 0.008004034033152708 33.0 16.0 2.294592562280499 3.0 0.1431907582204469 19.0 17.0 213.6 0.5089537262166648 11.0 100.3088715 52611.0 414576.0 27.0 507.9 14.0 21.0 0.15813924397456677 0.013571651533132646 1.2578363993574158 1.2690477637393385 0.4171807666145652 0.20632844144378837 5579.0 2.8 2.814924163482691 Richland 0.040771601 0.142314075103238 38.0 19.0 2.2945925623052963 45.0 0.1431907582262461 14.0 22.0 20.5 0.0 2.0 87.7404717 46019.0 20544.0 32.0 43.9 24.0 19.0 0.15813924396417445 0.0135

In [13]:
df.where( df['label'].isNull() ).count()

Out[327]: 0

In [14]:
df.where( df['pop_fraction'].isNull() ).count()

Out[328]: 30

In [15]:
#define a function to identify the count of nulls in the columns
def count_nulls(df):
    null_counts = []          #make an empty list to hold our results
    for col in df.dtypes:     #iterate through the column data types we saw above, e.g. ('C0', 'bigint')
        cname = col[0]        #splits out the column name, e.g. 'C0'    
        ctype = col[1]        #splits out the column type, e.g. 'bigint'
        if ctype != 'string': #skip processing string columns for efficiency (can't have nulls)
            nulls = df.where( df[cname].isNull() ).count()
            result = tuple([cname, nulls])  #new tuple, (column name, null count)
            null_counts.append(result)      #put the new tuple in our result list
    return null_counts

null_counts = count_nulls(df)

In [16]:
null_counts

Out[330]: [('Adult_obesity_percentage', 0),
 ('Adult_smoking_percentage', 0),
 ('All_Specialties_AAMC', 0),
 ('Clinical_Care_rank', 0),
 ('Emergency_Medicine_specialists_2019', 0),
 ('Excessive_drinking_percentage', 0),
 ('Health_Behaviors_rank', 0),
 ('House_per_sq_mile', 0),
 ('ICU_Beds', 0),
 ('Length_of_Life_rank', 0),
 ('Med_HH_Income_Percent_of_State_Total_2018', 0),
 ('Median_Household_Income_2018', 0),
 ('POP_ESTIMATE_2018', 30),
 ('Physical_Environment_rank', 0),
 ('Population_per_sq_mile', 0),
 ('Quality_of_Life_rank', 0),
 ('Social_Economic_Factors_rank', 0),
 ('Surgery_specialists_2019', 0),
 ('Total_Hospitals_2019', 0),
 ('Total_Primary_Care_Physicians_2019', 0),
 ('Total_Specialist_Physicians_2019', 0),
 ('Total_nurse_practitioners_2019', 0),
 ('Total_physician_assistants_2019', 0),
 ('Unemployed_2019', 0),
 ('Unemployment_rate_2019', 0),
 ('cases', 0),
 ('pop_fraction', 30),
 ('label', 0)]

In [17]:
display(df)

Adult_obesity_percentage Adult_smoking_percentage All_Specialties_AAMC Clinical_Care_rank Emergency_Medicine_specialists_2019 Excessive_drinking_percentage Health_Behaviors_rank House_per_sq_mile ICU_Beds Length_of_Life_rank Med_HH_Income_Percent_of_State_Total_2018 Median_Household_Income_2018 POP_ESTIMATE_2018 Physical_Environment_rank Population_per_sq_mile Quality_of_Life_rank Social_Economic_Factors_rank Surgery_specialists_2019 Total_Hospitals_2019 Total_Primary_Care_Physicians_2019 Total_Specialist_Physicians_2019 Total_nurse_practitioners_2019 Total_physician_assistants_2019 Unemployed_2019 Unemployment_rate_2019 cases county pop_fraction label 40.0 21.0 2.2945925621281065 41.0 0.14319075819624313 13.0 44.0 19.0 0.0 41.0 63.29767965 33199.0 17142.0 41.0 46.9 46.0 42.0 0.1581392439621981 0.013571651557577879 1.257836399486641 1.2690477639715319 0.4171807667133357 0.20632844143040488 266.0 4.0 7.117022517792556 Lee 0.001685835 0.5833625014584063 32.0 16.0 2.2945925621627485 6.0 0.14319075822283683 19.0 11.0 163.0 0.18642045608611948 9.0 115.5922897 60627.0 295032.0 7.0 375.4 10.0 3.0 0.158139243980314 0.013571651532715095 1.2578363994414166 1.2690477636324196 0.4171807668320725 0.20632844145719786 3510.0 2.3 1.667615716261287 Lexington 0.029015011 0.08473657094823613 44.0 20.0 2.294592562260382 44.0 0.14319075820741647 14.0 41.0 30.6 0.32217532781339603 40.0 65.52079163 34365.0 31039.0 19.0 67.6 45.0 43.0 0.15813924395115822 0.013571651535165435 1.2578363993685362 1.2690477637810496 0.41718076677728017 0.20632844144463416 564.0 4.3 1.5464415735043011 Marion 0.00305254 0.12887013112535842 39.0 21.0 2.294592562315327 39.0 0.1431907582013789 15.0 40.0 25.2 0.0 43.0 63.93639536 33534.0 26398.0 44.0 60.3 39.0 45.0 0.15813924395787562 0.013571651526630805 1.2578363993484354 1.2690477638457458 0.41718076672475185 0.20632844143495718 444.0 4.8 2.272899462080461 Marlboro 0.002596119 0.0 34.0 17.0 2.2945925621679066 4.0 0.14319075823591926 14.0 9.0 15.2 0.0 46.0 85.19323533 44683.0 9410.0 13.0 28.5 25.0 34.0 0.15813924399574922 0.013571651540913922 1.2578363995749204 1.2690477640807651 0.41718076673751325 0.206328441445271 104.0 3.1 0.7438894792773645 McCormick 9.25429E-4 0.10626992561105207 36.0 18.0 2.294592562305296 21.0 0.14319075822949118 16.0 23.0 28.4 0.181723779854621 10.0 91.57276592 48029.0 38520.0 16.0 59.5 21.0 15.0 0.1581392439771547 0.013571651531671856 1.2578363995327102 1.269047763759086 0.41718076661474557 0.2063284414330218 514.0 2.7 0.8047767393561787 Newberry 0.003788261 0.02596053997923157 32.0 17.0 2.2945925625845303 12.0 0.14319075815959373 16.0 14.0 61.9 0.15311200142904535 16.0 96.33930104 50529.0 78374.0 15.0 118.6 4.0 12.0 0.15813924400949295 0.01357165152984408 1.257836399443693 1.2690477637992192 0.41718076670834714 0.2063284414474188 971.0 2.8 0.49761400464439737 Oconee 0.007707715 0.0 41.0 17.0 2.294592562173603 26.0 0.14319075816136378 13.0 27.0 38.4 0.23005958543262706 34.0 70.80020591 37134.0 86934.0 37.0 83.6 38.0 38.0 0.15813924390917247 0.013571651528745943 1.2578363988773091 1.2690477638208295 0.41718076667356846 0.20632844146133847 1655.0 4.8 1.2193158027929234 Orangeburg 0.00854955 0.023005958543262706 32.0 17.0 2.294592562651576 7.0 0.14319075822214394 18.0 6.0 103.2 0.12006051049729063 12.0 93.03132567 48794.0 124937.0 33.0 240.2 8.0 9.0 0.1581392439389452 0.013571651536374333 1.257836399145169 1.2690477640730926 0.41718076670642007 0.20632844145449308 1604.0 2.8 0.6803428928179802 Pickens 0.012286967 0.008004034033152708 33.0 16.0 2.294592562280499 3.0 0.1431907582204469 19.0 17.0 213.6 0.5089537262166648 11.0 100.3088715 52611.0 414576.0 27.0 507.9 14.0 21.0 0.15813924397456677 0.013571651533132646 1.2578363993574158 1.2690477637393385 0.4171807666145652 0.20632844144378837 5579.0 2.8 2.814924163482691 Richland 0.040771601 0.142314075103238 38.0 19.0 2.2945925623052963 45.0 0.1431907582262461 14.0 22.0 20.5 0.0 2.0 87.7404717 46019.0 20544.0 32.0 43.9 24.0 19.0 0.15813924396417445 0.0135

In [18]:

df = df.drop("pop_fraction")
df_temp=df_temp.drop("pop_fraction")

In [20]:
label = df[['label']].collect()


In [21]:
print(label[:5])


[Row(label=0.5833625014584063), Row(label=0.08473657094823613), Row(label=0.12887013112535842), Row(label=0.0), Row(label=0.10626992561105207)]

In [22]:
df.columns


Out[335]: ['Adult_obesity_percentage',
 'Adult_smoking_percentage',
 'All_Specialties_AAMC',
 'Clinical_Care_rank',
 'Emergency_Medicine_specialists_2019',
 'Excessive_drinking_percentage',
 'Health_Behaviors_rank',
 'House_per_sq_mile',
 'ICU_Beds',
 'Length_of_Life_rank',
 'Med_HH_Income_Percent_of_State_Total_2018',
 'Median_Household_Income_2018',
 'POP_ESTIMATE_2018',
 'Physical_Environment_rank',
 'Population_per_sq_mile',
 'Quality_of_Life_rank',
 'Social_Economic_Factors_rank',
 'Surgery_specialists_2019',
 'Total_Hospitals_2019',
 'Total_Primary_Care_Physicians_2019',
 'Total_Specialist_Physicians_2019',
 'Total_nurse_practitioners_2019',
 'Total_physician_assistants_2019',
 'Unemployed_2019',
 'Unemployment_rate_2019',
 'cases',
 'county',
 'label']

In [23]:
df.dtypes

Out[336]: [('Adult_obesity_percentage', 'double'),
 ('Adult_smoking_percentage', 'double'),
 ('All_Specialties_AAMC', 'double'),
 ('Clinical_Care_rank', 'double'),
 ('Emergency_Medicine_specialists_2019', 'double'),
 ('Excessive_drinking_percentage', 'double'),
 ('Health_Behaviors_rank', 'double'),
 ('House_per_sq_mile', 'double'),
 ('ICU_Beds', 'double'),
 ('Length_of_Life_rank', 'double'),
 ('Med_HH_Income_Percent_of_State_Total_2018', 'double'),
 ('Median_Household_Income_2018', 'double'),
 ('POP_ESTIMATE_2018', 'double'),
 ('Physical_Environment_rank', 'double'),
 ('Population_per_sq_mile', 'double'),
 ('Quality_of_Life_rank', 'double'),
 ('Social_Economic_Factors_rank', 'double'),
 ('Surgery_specialists_2019', 'double'),
 ('Total_Hospitals_2019', 'double'),
 ('Total_Primary_Care_Physicians_2019', 'double'),
 ('Total_Specialist_Physicians_2019', 'double'),
 ('Total_nurse_practitioners_2019', 'double'),
 ('Total_physician_assistants_2019', 'double'),
 ('Unemployed_2019', 'double'),
 ('Unemployment_rate_2019', 'double'),
 ('cases', 'double'),
 ('county', 'string'),
 ('label', 'double')]

In [24]:
#drop county since it is string and is not a numerical feature
df = df.drop("county")
df_temp=df_temp.drop("county")


In [25]:
df = df.dropna()
df_temp=df_temp.dropna()

In [26]:
display(df)

Adult_obesity_percentage Adult_smoking_percentage All_Specialties_AAMC Clinical_Care_rank Emergency_Medicine_specialists_2019 Excessive_drinking_percentage Health_Behaviors_rank House_per_sq_mile ICU_Beds Length_of_Life_rank Med_HH_Income_Percent_of_State_Total_2018 Median_Household_Income_2018 POP_ESTIMATE_2018 Physical_Environment_rank Population_per_sq_mile Quality_of_Life_rank Social_Economic_Factors_rank Surgery_specialists_2019 Total_Hospitals_2019 Total_Primary_Care_Physicians_2019 Total_Specialist_Physicians_2019 Total_nurse_practitioners_2019 Total_physician_assistants_2019 Unemployed_2019 Unemployment_rate_2019 cases label 40.0 21.0 2.2945925621281065 41.0 0.14319075819624313 13.0 44.0 19.0 0.0 41.0 63.29767965 33199.0 17142.0 41.0 46.9 46.0 42.0 0.1581392439621981 0.013571651557577879 1.257836399486641 1.2690477639715319 0.4171807667133357 0.20632844143040488 266.0 4.0 7.117022517792556 0.5833625014584063 32.0 16.0 2.2945925621627485 6.0 0.14319075822283683 19.0 11.0 163.0 0.18642045608611948 9.0 115.5922897 60627.0 295032.0 7.0 375.4 10.0 3.0 0.158139243980314 0.013571651532715095 1.2578363994414166 1.2690477636324196 0.4171807668320725 0.20632844145719786 3510.0 2.3 1.667615716261287 0.08473657094823613 44.0 20.0 2.294592562260382 44.0 0.14319075820741647 14.0 41.0 30.6 0.32217532781339603 40.0 65.52079163 34365.0 31039.0 19.0 67.6 45.0 43.0 0.15813924395115822 0.013571651535165435 1.2578363993685362 1.2690477637810496 0.41718076677728017 0.20632844144463416 564.0 4.3 1.5464415735043011 0.12887013112535842 39.0 21.0 2.294592562315327 39.0 0.1431907582013789 15.0 40.0 25.2 0.0 43.0 63.93639536 33534.0 26398.0 44.0 60.3 39.0 45.0 0.15813924395787562 0.013571651526630805 1.2578363993484354 1.2690477638457458 0.41718076672475185 0.20632844143495718 444.0 4.8 2.272899462080461 0.0 34.0 17.0 2.2945925621679066 4.0 0.14319075823591926 14.0 9.0 15.2 0.0 46.0 85.19323533 44683.0 9410.0 13.0 28.5 25.0 34.0 0.15813924399574922 0.013571651540913922 1.2578363995749204 1.2690477640807651 0.41718076673751325 0.206328441445271 104.0 3.1 0.7438894792773645 0.10626992561105207 36.0 18.0 2.294592562305296 21.0 0.14319075822949118 16.0 23.0 28.4 0.181723779854621 10.0 91.57276592 48029.0 38520.0 16.0 59.5 21.0 15.0 0.1581392439771547 0.013571651531671856 1.2578363995327102 1.269047763759086 0.41718076661474557 0.2063284414330218 514.0 2.7 0.8047767393561787 0.02596053997923157 32.0 17.0 2.2945925625845303 12.0 0.14319075815959373 16.0 14.0 61.9 0.15311200142904535 16.0 96.33930104 50529.0 78374.0 15.0 118.6 4.0 12.0 0.15813924400949295 0.01357165152984408 1.257836399443693 1.2690477637992192 0.41718076670834714 0.2063284414474188 971.0 2.8 0.49761400464439737 0.0 41.0 17.0 2.294592562173603 26.0 0.14319075816136378 13.0 27.0 38.4 0.23005958543262706 34.0 70.80020591 37134.0 86934.0 37.0 83.6 38.0 38.0 0.15813924390917247 0.013571651528745943 1.2578363988773091 1.2690477638208295 0.41718076667356846 0.20632844146133847 1655.0 4.8 1.2193158027929234 0.023005958543262706 32.0 17.0 2.294592562651576 7.0 0.14319075822214394 18.0 6.0 103.2 0.12006051049729063 12.0 93.03132567 48794.0 124937.0 33.0 240.2 8.0 9.0 0.1581392439389452 0.013571651536374333 1.257836399145169 1.2690477640730926 0.41718076670642007 0.20632844145449308 1604.0 2.8 0.6803428928179802 0.008004034033152708 33.0 16.0 2.294592562280499 3.0 0.1431907582204469 19.0 17.0 213.6 0.5089537262166648 11.0 100.3088715 52611.0 414576.0 27.0 507.9 14.0 21.0 0.15813924397456677 0.013571651533132646 1.2578363993574158 1.2690477637393385 0.4171807666145652 0.20632844144378837 5579.0 2.8 2.814924163482691 0.142314075103238 38.0 19.0 2.2945925623052963 45.0 0.1431907582262461 14.0 22.0 20.5 0.0 2.0 87.7404717 46019.0 20544.0 32.0 43.9 24.0 19.0 0.15813924396417445 0.013571651528426789 1.2578363994353583 1.2690477638239874 0.4171807667445483 0.20632844144275703 238.0 2.7 4.478193146417445 0.0 32.0 17.0 2.294592562315221 9.0 0.1431907582322357 16.0 15.0 151.8 0.12424813946375778 19.0 102.1

In [27]:
df.count()

Out[340]: 2890

In [28]:
df_temp.count()

Out[341]: 2890

In [29]:
from pyspark.ml.linalg import Vectors
from pyspark.ml import Pipeline
from pyspark.ml.regression import GBTRegressor, GeneralizedLinearRegression, AFTSurvivalRegression
from pyspark.ml.feature import VectorIndexer

from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.sql.types import DoubleType
 
from pyspark.ml.feature import StringIndexer, VectorAssembler, OneHotEncoder  

In [30]:
valuableColumns = list(df.columns)

In [31]:
valuableColumns

Out[344]: ['Adult_obesity_percentage',
 'Adult_smoking_percentage',
 'All_Specialties_AAMC',
 'Clinical_Care_rank',
 'Emergency_Medicine_specialists_2019',
 'Excessive_drinking_percentage',
 'Health_Behaviors_rank',
 'House_per_sq_mile',
 'ICU_Beds',
 'Length_of_Life_rank',
 'Med_HH_Income_Percent_of_State_Total_2018',
 'Median_Household_Income_2018',
 'POP_ESTIMATE_2018',
 'Physical_Environment_rank',
 'Population_per_sq_mile',
 'Quality_of_Life_rank',
 'Social_Economic_Factors_rank',
 'Surgery_specialists_2019',
 'Total_Hospitals_2019',
 'Total_Primary_Care_Physicians_2019',
 'Total_Specialist_Physicians_2019',
 'Total_nurse_practitioners_2019',
 'Total_physician_assistants_2019',
 'Unemployed_2019',
 'Unemployment_rate_2019',
 'cases',
 'label']

In [32]:
from pyspark.ml import Pipeline
from pyspark.ml.regression import DecisionTreeRegressor
from pyspark.ml.feature import VectorIndexer
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.sql import Row
from pyspark.ml.linalg import Vectors

In [33]:
df=df.rdd.map(lambda x:(Vectors.dense(x[0:-1]), x[-1])).toDF(["features", "label"])
df.show()

+--------------------+--------------------+
 features| label|
+--------------------+--------------------+
[40.0,21.0,2.2945...| 0.5833625014584063|
[32.0,16.0,2.2945...| 0.08473657094823613|
[44.0,20.0,2.2945...| 0.12887013112535842|
[39.0,21.0,2.2945...| 0.0|
[34.0,17.0,2.2945...| 0.10626992561105207|
[36.0,18.0,2.2945...| 0.02596053997923157|
[32.0,17.0,2.2945...| 0.0|
[41.0,17.0,2.2945...|0.023005958543262706|
[32.0,17.0,2.2945...|0.008004034033152708|
[33.0,16.0,2.2945...| 0.142314075103238|
[38.0,19.0,2.2945...| 0.0|
[32.0,17.0,2.2945...| 0.04141604648791926|
[38.0,18.0,2.2945...| 0.1220519753642782|
[39.0,19.0,2.2945...| 0.0|
[42.0,19.0,2.2945...| 0.2940599882376005|
[32.0,15.0,2.2945...|0.018240319862249103|
[37.0,12.0,2.4041...| 0.0|
[36.0,16.0,2.4041...| 0.10591537361648043|
[40.0,15.0,2.4041...| 0.0|
[28.0,13.0,2.4041...| 0.0|
+--------------------+--------------------+
only showing top 20 rows

In [34]:
# Automatically identify categorical features, and index them.
# We specify maxCategories so features with > 4 distinct values are treated as continuous.
featureIndexer = VectorIndexer(inputCol="features", outputCol="indexedFeatures", maxCategories=4).fit(df)

In [35]:
# Split the data into training and test sets (30% held out for testing)
(trainingData, testData) = df.randomSplit([0.7, 0.3])

In [36]:
# Train a DecisionTree model.
dt = DecisionTreeRegressor(featuresCol="indexedFeatures")

In [37]:
# Chain indexer and tree in a Pipeline
pipeline = Pipeline(stages=[featureIndexer, dt])

In [38]:
# Train model.  This also runs the indexer.
model = pipeline.fit(trainingData)


In [39]:
# Make predictions.
predictions = model.transform(testData)

# Select example rows to display.
predictions.select("prediction", "label", "features").show(5)

+--------------------+-------------------+--------------------+
 prediction| label| features|
+--------------------+-------------------+--------------------+
 0.2622086316551539| 0.2724300762804214|[22.0,23.0,2.5307...|
 0.04345882288466045| 0.0|[24.0,17.0,2.2483...|
 0.06611770559389846|0.03973891532630617|[25.0,13.0,2.2483...|
0.022519838491280055| 0.0|[25.0,18.0,2.2483...|
0.014947738508470634| 0.0|[25.0,18.0,2.2483...|
+--------------------+-------------------+--------------------+
only showing top 5 rows

In [40]:
display(predictions)

features label indexedFeatures prediction List(1, 26, List(), List(22.0, 23.0, 2.530720043588812, 90.0, 0.12289494406102433, 17.0, 34.0, 29.5, 0.0, 53.0, 94.10686323, 49280.0, 11012.0, 21.0, 68.9, 35.0, 25.0, 0.17326414584090083, 0.016986680984380675, 1.311076350345078, 1.4923168507083182, 0.8490386276788958, 0.17607064093715946, 168.0, 3.1, 125.40864511442064)) 0.2724300762804214 List(1, 26, List(), List(22.0, 23.0, 2.530720043588812, 90.0, 0.12289494406102433, 17.0, 34.0, 29.5, 0.0, 53.0, 94.10686323, 49280.0, 11012.0, 21.0, 68.9, 35.0, 25.0, 0.17326414584090083, 0.016986680984380675, 1.311076350345078, 1.4923168507083182, 0.8490386276788958, 0.17607064093715946, 168.0, 3.1, 125.40864511442064)) 0.2622086316551539 List(1, 26, List(), List(24.0, 17.0, 2.248392046368266, 186.0, 0.11354670758509783, 17.0, 143.0, 3.6, 0.0, 185.0, 71.0581871, 43084.0, 7462.0, 52.0, 8.8, 200.0, 210.0, 0.12114203805950148, 0.01822182511391048, 1.0697570139372823, 1.1810390586974002, 0.34492556137764674, 0.20357576320021442, 97.0, 3.7, 1.7421602787456445)) 0.0 List(1, 26, List(), List(24.0, 17.0, 2.248392046368266, 186.0, 0.11354670758509783, 17.0, 143.0, 3.6, 0.0, 185.0, 71.0581871, 43084.0, 7462.0, 52.0, 8.8, 200.0, 210.0, 0.12114203805950148, 0.01822182511391048, 1.0697570139372823, 1.1810390586974002, 0.34492556137764674, 0.20357576320021442, 97.0, 3.7, 1.7421602787456445)) 0.04345882288466045 List(1, 26, List(), List(25.0, 13.0, 2.2483920462560976, 7.0, 0.11354670753151794, 21.0, 20.0, 219.9, 0.05960837298945925, 6.0, 169.6430928, 102858.0, 100657.0, 144.0, 616.7, 10.0, 1.0, 0.1211420381096198, 0.01822182510903365, 1.0697570134218186, 1.1810390583864012, 0.3449255613618526, 0.20357576313619521, 1601.0, 3.1, 1.1524285444628788)) 0.03973891532630617 List(1, 26, List(), List(25.0, 13.0, 2.2483920462560976, 7.0, 0.11354670753151794, 21.0, 20.0, 219.9, 0.05960837298945925, 6.0, 169.6430928, 102858.0, 100657.0, 144.0, 616.7, 10.0, 1.0, 0.1211420381096198, 0.01822182510903365, 1.0697570134218186, 1.1810390583864012, 0.3449255613618526, 0.20357576313619521, 1601.0, 3.1, 1.1524285444628788)) 0.06611770559389846 List(1, 26, List(), List(25.0, 18.0, 2.24839204583711, 127.0, 0.11354670754024775, 16.0, 210.0, 9.4, 0.0, 191.0, 65.20154374, 39533.0, 23169.0, 232.0, 19.3, 211.0, 201.0, 0.12114203806810823, 0.018221825111139886, 1.069757013682075, 1.1810390586559627, 0.34492556139669384, 0.203575763174932, 325.0, 3.1, 0.9063835297164314)) 0.0 List(1, 26, List(), List(25.0, 18.0, 2.24839204583711, 127.0, 0.11354670754024775, 16.0, 210.0, 9.4, 0.0, 191.0, 65.20154374, 39533.0, 23169.0, 232.0, 19.3, 211.0, 201.0, 0.12114203806810823, 0.018221825111139886, 1.069757013682075, 1.1810390586559627, 0.34492556139669384, 0.203575763174932, 325.0, 3.1, 0.9063835297164314)) 0.022519838491280055 List(1, 26, List(), List(25.0, 18.0, 2.24839204583921, 215.0, 0.11354670768688294, 15.0, 123.0, 1.8, 0.0, 243.0, 70.71018604, 42873.0, 2836.0, 84.0, 4.0, 230.0, 202.0, 0.12114203808180535, 0.018221825105782793, 1.0697570137517631, 1.1810390585331454, 0.3449255613540198, 0.20357576304654443, 38.0, 3.4, 0.3526093088857546)) 0.0 List(1, 26, List(), List(25.0, 18.0, 2.24839204583921, 215.0, 0.11354670768688294, 15.0, 123.0, 1.8, 0.0, 243.0, 70.71018604, 42873.0, 2836.0, 84.0, 4.0, 230.0, 202.0, 0.12114203808180535, 0.018221825105782793, 1.0697570137517631, 1.1810390585331454, 0.3449255613540198, 0.20357576304654443, 38.0, 3.4, 0.3526093088857546)) 0.014947738508470634 List(1, 26, List(), List(25.0, 19.0, 2.5307200436749335, 37.0, 0.12289494400249572, 15.0, 2.0, 22.6, 0.0, 3.0, 111.2057442, 58234.0, 6411.0, 52.0, 49.2, 2.0, 7.0, 0.1732641458430822, 0.016986681017002028, 1.3110763500233973, 1.4923168504133522, 0.8490386276711901, 0.17607064092965216, 106.0, 2.9, 0.4679457182966776)) 0.0 List(1, 26, List(), List(25.0, 19.0, 2.5307200436749335, 37.0, 0.12289494400249572, 15.0, 2.0, 22.6, 0.0, 3.0, 111.2057442, 58234.0, 6411.0, 52.0, 49.2, 2.0, 7.0, 0.1732641458430822, 0.016986681017002028, 

In [41]:
predictions.dtypes

Out[354]: [('features', 'vector'),
 ('label', 'double'),
 ('indexedFeatures', 'vector'),
 ('prediction', 'double')]

In [42]:

pandas_df_temp = df_temp.toPandas()
pandas_predictions = predictions.toPandas()



In [43]:
display(pandas_predictions)

features label indexedFeatures prediction List(1, 26, List(), List(22.0, 23.0, 2.530720043588812, 90.0, 0.12289494406102433, 17.0, 34.0, 29.5, 0.0, 53.0, 94.10686323, 49280.0, 11012.0, 21.0, 68.9, 35.0, 25.0, 0.17326414584090083, 0.016986680984380675, 1.311076350345078, 1.4923168507083182, 0.8490386276788958, 0.17607064093715946, 168.0, 3.1, 125.40864511442064)) 0.2724300762804214 List(1, 26, List(), List(22.0, 23.0, 2.530720043588812, 90.0, 0.12289494406102433, 17.0, 34.0, 29.5, 0.0, 53.0, 94.10686323, 49280.0, 11012.0, 21.0, 68.9, 35.0, 25.0, 0.17326414584090083, 0.016986680984380675, 1.311076350345078, 1.4923168507083182, 0.8490386276788958, 0.17607064093715946, 168.0, 3.1, 125.40864511442064)) 0.2622086316551539 List(1, 26, List(), List(24.0, 17.0, 2.248392046368266, 186.0, 0.11354670758509783, 17.0, 143.0, 3.6, 0.0, 185.0, 71.0581871, 43084.0, 7462.0, 52.0, 8.8, 200.0, 210.0, 0.12114203805950148, 0.01822182511391048, 1.0697570139372823, 1.1810390586974002, 0.34492556137764674, 0.20357576320021442, 97.0, 3.7, 1.7421602787456445)) 0.0 List(1, 26, List(), List(24.0, 17.0, 2.248392046368266, 186.0, 0.11354670758509783, 17.0, 143.0, 3.6, 0.0, 185.0, 71.0581871, 43084.0, 7462.0, 52.0, 8.8, 200.0, 210.0, 0.12114203805950148, 0.01822182511391048, 1.0697570139372823, 1.1810390586974002, 0.34492556137764674, 0.20357576320021442, 97.0, 3.7, 1.7421602787456445)) 0.04345882288466045 List(1, 26, List(), List(25.0, 13.0, 2.2483920462560976, 7.0, 0.11354670753151794, 21.0, 20.0, 219.9, 0.05960837298945925, 6.0, 169.6430928, 102858.0, 100657.0, 144.0, 616.7, 10.0, 1.0, 0.1211420381096198, 0.01822182510903365, 1.0697570134218186, 1.1810390583864012, 0.3449255613618526, 0.20357576313619521, 1601.0, 3.1, 1.1524285444628788)) 0.03973891532630617 List(1, 26, List(), List(25.0, 13.0, 2.2483920462560976, 7.0, 0.11354670753151794, 21.0, 20.0, 219.9, 0.05960837298945925, 6.0, 169.6430928, 102858.0, 100657.0, 144.0, 616.7, 10.0, 1.0, 0.1211420381096198, 0.01822182510903365, 1.0697570134218186, 1.1810390583864012, 0.3449255613618526, 0.20357576313619521, 1601.0, 3.1, 1.1524285444628788)) 0.06611770559389846 List(1, 26, List(), List(25.0, 18.0, 2.24839204583711, 127.0, 0.11354670754024775, 16.0, 210.0, 9.4, 0.0, 191.0, 65.20154374, 39533.0, 23169.0, 232.0, 19.3, 211.0, 201.0, 0.12114203806810823, 0.018221825111139886, 1.069757013682075, 1.1810390586559627, 0.34492556139669384, 0.203575763174932, 325.0, 3.1, 0.9063835297164314)) 0.0 List(1, 26, List(), List(25.0, 18.0, 2.24839204583711, 127.0, 0.11354670754024775, 16.0, 210.0, 9.4, 0.0, 191.0, 65.20154374, 39533.0, 23169.0, 232.0, 19.3, 211.0, 201.0, 0.12114203806810823, 0.018221825111139886, 1.069757013682075, 1.1810390586559627, 0.34492556139669384, 0.203575763174932, 325.0, 3.1, 0.9063835297164314)) 0.022519838491280055 List(1, 26, List(), List(25.0, 18.0, 2.24839204583921, 215.0, 0.11354670768688294, 15.0, 123.0, 1.8, 0.0, 243.0, 70.71018604, 42873.0, 2836.0, 84.0, 4.0, 230.0, 202.0, 0.12114203808180535, 0.018221825105782793, 1.0697570137517631, 1.1810390585331454, 0.3449255613540198, 0.20357576304654443, 38.0, 3.4, 0.3526093088857546)) 0.0 List(1, 26, List(), List(25.0, 18.0, 2.24839204583921, 215.0, 0.11354670768688294, 15.0, 123.0, 1.8, 0.0, 243.0, 70.71018604, 42873.0, 2836.0, 84.0, 4.0, 230.0, 202.0, 0.12114203808180535, 0.018221825105782793, 1.0697570137517631, 1.1810390585331454, 0.3449255613540198, 0.20357576304654443, 38.0, 3.4, 0.3526093088857546)) 0.014947738508470634 List(1, 26, List(), List(25.0, 19.0, 2.5307200436749335, 37.0, 0.12289494400249572, 15.0, 2.0, 22.6, 0.0, 3.0, 111.2057442, 58234.0, 6411.0, 52.0, 49.2, 2.0, 7.0, 0.1732641458430822, 0.016986681017002028, 1.3110763500233973, 1.4923168504133522, 0.8490386276711901, 0.17607064092965216, 106.0, 2.9, 0.4679457182966776)) 0.0 List(1, 26, List(), List(25.0, 19.0, 2.5307200436749335, 37.0, 0.12289494400249572, 15.0, 2.0, 22.6, 0.0, 3.0, 111.2057442, 58234.0, 6411.0, 52.0, 49.2, 2.0, 7.0, 0.1732641458430822, 0.016986681017002028, 

In [44]:
display(pandas_df_temp)

cases deaths POP_ESTIMATE_2018 All_Specialties_AAMC Total_nurse_practitioners_2019 Total_physician_assistants_2019 Total_Hospitals_2019 Total_Primary_Care_Physicians_2019 Surgery_specialists_2019 Emergency_Medicine_specialists_2019 Total_Specialist_Physicians_2019 ICU_Beds Length_of_Life_rank Quality_of_Life_rank Health_Behaviors_rank Clinical_Care_rank Social_Economic_Factors_rank Physical_Environment_rank Adult_smoking_percentage Adult_obesity_percentage Excessive_drinking_percentage Population_per_sq_mile House_per_sq_mile Unemployed_2019 Unemployment_rate_2019 Median_Household_Income_2018 Med_HH_Income_Percent_of_State_Total_2018 7.117022517792556 0.5833625014584063 17142.0 2.2945925621281065 0.4171807667133357 0.20632844143040488 0.013571651557577879 1.257836399486641 0.1581392439621981 0.14319075819624313 1.2690477639715319 0.0 41.0 46.0 44.0 41.0 42.0 41.0 21.0 40.0 13.0 46.9 19.0 266.0 4.0 33199.0 63.29767965 1.667615716261287 0.08473657094823613 295032.0 2.2945925621627485 0.4171807668320725 0.20632844145719786 0.013571651532715095 1.2578363994414166 0.158139243980314 0.14319075822283683 1.2690477636324196 0.18642045608611948 9.0 10.0 11.0 6.0 3.0 7.0 16.0 32.0 19.0 375.4 163.0 3510.0 2.3 60627.0 115.5922897 1.5464415735043011 0.12887013112535842 31039.0 2.294592562260382 0.41718076677728017 0.20632844144463416 0.013571651535165435 1.2578363993685362 0.15813924395115822 0.14319075820741647 1.2690477637810496 0.32217532781339603 40.0 45.0 41.0 44.0 43.0 19.0 20.0 44.0 14.0 67.6 30.6 564.0 4.3 34365.0 65.52079163 2.272899462080461 0.0 26398.0 2.294592562315327 0.41718076672475185 0.20632844143495718 0.013571651526630805 1.2578363993484354 0.15813924395787562 0.1431907582013789 1.2690477638457458 0.0 43.0 39.0 40.0 39.0 45.0 44.0 21.0 39.0 15.0 60.3 25.2 444.0 4.8 33534.0 63.93639536 0.7438894792773645 0.10626992561105207 9410.0 2.2945925621679066 0.41718076673751325 0.206328441445271 0.013571651540913922 1.2578363995749204 0.15813924399574922 0.14319075823591926 1.2690477640807651 0.0 46.0 25.0 9.0 4.0 34.0 13.0 17.0 34.0 14.0 28.5 15.2 104.0 3.1 44683.0 85.19323533 0.8047767393561787 0.02596053997923157 38520.0 2.294592562305296 0.41718076661474557 0.2063284414330218 0.013571651531671856 1.2578363995327102 0.1581392439771547 0.14319075822949118 1.269047763759086 0.181723779854621 10.0 21.0 23.0 21.0 15.0 16.0 18.0 36.0 16.0 59.5 28.4 514.0 2.7 48029.0 91.57276592 0.49761400464439737 0.0 78374.0 2.2945925625845303 0.41718076670834714 0.2063284414474188 0.01357165152984408 1.257836399443693 0.15813924400949295 0.14319075815959373 1.2690477637992192 0.15311200142904535 16.0 4.0 14.0 12.0 12.0 15.0 17.0 32.0 16.0 118.6 61.9 971.0 2.8 50529.0 96.33930104 1.2193158027929234 0.023005958543262706 86934.0 2.294592562173603 0.41718076667356846 0.20632844146133847 0.013571651528745943 1.2578363988773091 0.15813924390917247 0.14319075816136378 1.2690477638208295 0.23005958543262706 34.0 38.0 27.0 26.0 38.0 37.0 17.0 41.0 13.0 83.6 38.4 1655.0 4.8 37134.0 70.80020591 0.6803428928179802 0.008004034033152708 124937.0 2.294592562651576 0.41718076670642007 0.20632844145449308 0.013571651536374333 1.257836399145169 0.1581392439389452 0.14319075822214394 1.2690477640730926 0.12006051049729063 12.0 8.0 6.0 7.0 9.0 33.0 17.0 32.0 18.0 240.2 103.2 1604.0 2.8 48794.0 93.03132567 2.814924163482691 0.142314075103238 414576.0 2.294592562280499 0.4171807666145652 0.20632844144378837 0.013571651533132646 1.2578363993574158 0.15813924397456677 0.1431907582204469 1.2690477637393385 0.5089537262166648 11.0 14.0 17.0 3.0 21.0 27.0 16.0 33.0 19.0 507.9 213.6 5579.0 2.8 52611.0 100.3088715 4.478193146417445 0.0 20544.0 2.2945925623052963 0.4171807667445483 0.20632844144275703 0.013571651528426789 1.2578363994353583 0.15813924396417445 0.1431907582262461 1.2690477638239874 0.0 2.0 24.0 22.0 45.0 19.0 32.0 19.0 38.0 14.0 43.9 20.5 238.0 2.7 46019.0 87.7404717 1.1277908043633398 0.04141604648791926 313888.0 2.294592562315221 0.417180766706596 0.2063284414

--------------------------------------------------------------------------- 
 OptionError Traceback (most recent call last)
 <command-3104795268426953> in <module> 
 ----> 1 pandas_predictions [ 'prediction_de_nom' ] = ( pandas_predictions [ 'prediction' ] * pandas_df_temp [ 'POP_ESTIMATE_2018' ] ) / 1000 

 /databricks/python/lib/python3.7/site-packages/pandas/core/ops.py in wrapper (left, right) 

 /databricks/python/lib/python3.7/site-packages/pandas/core/ops.py in safe_na_op (lvalues, rvalues) 

 /databricks/python/lib/python3.7/site-packages/pandas/core/ops.py in na_op (x, y) 

 /databricks/python/lib/python3.7/site-packages/pandas/core/computation/expressions.py in <module> 
 155 
 156 # turn myself on 
 --> 157 set_use_numexpr ( get_option ( "compute.use_numexpr" ) ) 
 158 
 159 

 /databricks/python/lib/python3.7/site-packages/pandas/_config/config.py in __call__ (self, *args, **kwds) 
 229 
 230 def __call__ ( self , * args , ** kwds ) : 
 --> 231 return self . __func__ ( * args , ** kwds ) 
 232 
 233 @ property

 /databricks/python/lib/python3.7/site-packages/pandas/_config/config.py in _get_option (pat, silent) 
 100 
 101 def _get_option ( pat , silent = False ) : 
 --> 102 key = _get_single_key ( pat , silent ) 
 103 
 104 # walk the nested dict 

 /databricks/python/lib/python3.7/site-packages/pandas/_config/config.py in _get_single_key (pat, silent) 
 86 if not silent : 
 87 _warn_if_deprecated ( pat ) 
 ---> 88 raise OptionError ( f"No such keys(s): {repr(pat)}" ) 
 89 if len ( keys ) > 1 : 
 90 raise OptionError ( "Pattern matched multiple keys" ) 

 OptionError : "No such keys(s): 'compute.use_numexpr'"

In [46]:
pandas_predictions['prediction_de_nom'] = (pandas_predictions['prediction']*pandas_df_temp['POP_ESTIMATE_2018'])/1000)

File "<command-3104795268426941>" , line 1 
 pandas_predictions['prediction_de_nom'] = (pandas_predictions['prediction']*pandas_df_temp['POP_ESTIMATE_2018'])/1000) 
 ^
 SyntaxError : invalid syntax

In [47]:
pandas_predictions['label_de_nom'] = (pandas_predictions['label']*pandas_df_temp['POP_ESTIMATE_2018'])/1000

--------------------------------------------------------------------------- 
 OptionError Traceback (most recent call last)
 <command-3104795268426952> in <module> 
 ----> 1 pandas_predictions [ 'label_de_nom' ] = ( pandas_predictions [ 'label' ] * pandas_df_temp [ 'POP_ESTIMATE_2018' ] ) / 1000 

 /databricks/python/lib/python3.7/site-packages/pandas/core/ops.py in wrapper (left, right) 

 /databricks/python/lib/python3.7/site-packages/pandas/core/ops.py in safe_na_op (lvalues, rvalues) 

 /databricks/python/lib/python3.7/site-packages/pandas/core/ops.py in na_op (x, y) 

 /databricks/python/lib/python3.7/site-packages/pandas/core/computation/expressions.py in <module> 
 155 
 156 # turn myself on 
 --> 157 set_use_numexpr ( get_option ( "compute.use_numexpr" ) ) 
 158 
 159 

 /databricks/python/lib/python3.7/site-packages/pandas/_config/config.py in __call__ (self, *args, **kwds) 
 229 
 230 def __call__ ( self , * args , ** kwds ) : 
 --> 231 return self . __func__ ( * args , ** kwds ) 
 232 
 233 @ property

 /databricks/python/lib/python3.7/site-packages/pandas/_config/config.py in _get_option (pat, silent) 
 100 
 101 def _get_option ( pat , silent = False ) : 
 --> 102 key = _get_single_key ( pat , silent ) 
 103 
 104 # walk the nested dict 

 /databricks/python/lib/python3.7/site-packages/pandas/_config/config.py in _get_single_key (pat, silent) 
 86 if not silent : 
 87 _warn_if_deprecated ( pat ) 
 ---> 88 raise OptionError ( f"No such keys(s): {repr(pat)}" ) 
 89 if len ( keys ) > 1 : 
 90 raise OptionError ( "Pattern matched multiple keys" ) 

 OptionError : "No such keys(s): 'compute.use_numexpr'"

In [48]:
pandas_predictions['prediction_de_nom'] = pandas_predictions['prediction_de_nom'].apply(lambda x: round(x))

In [49]:
pandas_predictions['label_de_nom'] = pandas_predictions['label_de_nom'].apply(lambda x: round(x))

In [50]:
# Select (prediction, true label) and compute test error
evaluator = RegressionEvaluator(
    labelCol="label", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions)
print("Root Mean Squared Error (RMSE) on test data = %g" % rmse)

In [51]:
treeModel = model.stages[1]
# summary only
print(treeModel)

In [52]:
display(treeModel)

In [53]:
#print the nodes of the decision tree model
print(treeModel.toDebugString)

In [54]:
def extract_feature_imp(feature_imp, dataset, features_col): 
  """Affiche pour chaque features d'un modèle son nom correspondant et les trie dans l'ordre d'importance""" 
  list_extract = [] 
  for i in dataset.schema[features_col].metadata["ml_attr"]["attrs"]: 
    list_extract = list_extract + dataset.schema[features_col].metadata["ml_attr"]["attrs"][i] 
    varlist = pd.DataFrame(list_extract) 
    varlist['score'] = varlist['idx'].apply(lambda x: feature_imp[x]) * 100 
    return varlist.sort_values('score', ascending=False)

In [56]:
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder

In [57]:
grid = ParamGridBuilder() \
  .addGrid(dt.maxDepth, [2, 3, 4, 5, 6, 7, 8]) \
  .addGrid(dt.maxBins, [2, 4, 8]) \
  .build()

In [58]:
cv = CrossValidator(estimator=pipeline, evaluator=evaluator, estimatorParamMaps=grid, numFolds=3)

In [59]:
# Explicitly create a new run.
# This allows this cell to be run multiple times.
# If you omit mlflow.start_run(), then this cell could run once,
# but a second run would hit conflicts when attempting to overwrite the first run.
import mlflow
import mlflow
import mlflow.mleap
import pyspark
#import pyspark.ml.mleap.SparkUtil 
#import mlflow.mleap.SparkUtil 
import mlflow.mleap
with mlflow.start_run():
  cvModel = cv.fit(trainingData)
  mlflow.set_tag('owner_team', 'UX Data Science') # Logs user-defined tags
  test_metric = evaluator.evaluate(cvModel.transform(testData))
  mlflow.log_metric('testData_' + evaluator.getMetricName(), test_metric) # Logs additional metrics
  mlflow.mleap.log_model(spark_model=cvModel.bestModel, sample_input=testData, artifact_path='dbfs:/databricks/mlflow/2835302286394144') # Logs the best model via mleap


In [60]:
import mlflow
import mlflow.mleap
from mlflow import log_metric, log_param, log_artifacts
def fit_model():
  import mlflow
  import mlflow.mleap
  from mlflow import log_metric, log_param, log_artifacts
  # Start a new MLflow run
  with mlflow.start_run() as run:
    # Fit the model, performing cross validation to improve accuracy
    grid = ParamGridBuilder().addGrid(dt.maxDepth, [2, 3, 4, 5, 6, 7, 8]).addGrid(dt.maxBins, [2, 4, 8]).build()
    #paramGrid = ParamGridBuilder().addGrid(hashingTF.numFeatures, [1000, 2000]).build()
    cv = CrossValidator(estimator=pipeline, evaluator=evaluator, estimatorParamMaps=grid, numFolds=3)
    #cv = CrossValidator(estimator=pipeline, evaluator=MulticlassClassificationEvaluator(), estimatorParamMaps=paramGrid)
    cvModel = cv.fit(trainingData)
    #cvModel = cv.fit(df)
    model = cvModel.bestModel
  
    # Log the model within the MLflow run
    mlflow.mleap.log_model(spark_model=model, sample_input=trainingData, artifact_path="dbfs:/databricks/mlflow/2835302286394144")

In [61]:
fit_model()